In [1]:
import pandas as pd
from intbitset import intbitset 
import numpy as np

In [2]:
x = intbitset([1,3,6])


In [3]:
df = pd.DataFrame([[{"bread"}, {1,4,5,7,8,9}], [{"butter"}, {1,2,3,4,6,8,9}], [{"milk"}, {3,5,6,7,8,9}], [{"coke"}, {2,4}], [{"jam"}, {1,8}]],columns=['food_item','TID'])

In [4]:
df    # testing 

food_item                    TID
0   {bread}     {1, 4, 5, 7, 8, 9}
1  {butter}  {1, 2, 3, 4, 6, 8, 9}
2    {milk}     {3, 5, 6, 7, 8, 9}
3    {coke}                 {2, 4}
4     {jam}                 {8, 1}

In [5]:
%load_ext Cython
%load_ext line_profiler
%load_ext memory_profiler

In [6]:
data_dict2 = df.to_dict(orient='index') 


In [7]:
data_dict2

{0: {'food_item': {'bread'}, 'TID': {1, 4, 5, 7, 8, 9}},
 1: {'food_item': {'butter'}, 'TID': {1, 2, 3, 4, 6, 8, 9}},
 2: {'food_item': {'milk'}, 'TID': {3, 5, 6, 7, 8, 9}},
 3: {'food_item': {'coke'}, 'TID': {2, 4}},
 4: {'food_item': {'jam'}, 'TID': {1, 8}}}

In [8]:
#### How I get a list of the TID sets within my implementtion 

from itertools import combinations, starmap, filterfalse, islice

def nth(iterable, n, default=None):
    "Returns the nth item or a default value"
    return next(islice(iterable, n, None), default)


tid_list = []
food_item_list = []
for elem in data_dict2:
    tid_list.append(data_dict2[elem]['TID'])
    food_item_list.append(data_dict2[elem]['food_item'])
    
tid_list



[{1, 4, 5, 7, 8, 9}, {1, 2, 3, 4, 6, 8, 9}, {3, 5, 6, 7, 8, 9}, {2, 4}, {1, 8}]

In [9]:
### Doing one iteration of eclat, this is the meat and potatos of my code. Normally we do an if check and throw out everything of 
# len <= min_support but that check isn't listed here to show you what this is doing 



min_support = 2


    

#from itertools import combinations, starmap, filterfalse

def intersect_minsupp(*a):
    returned_set = set.intersection(*a)
    if len(returned_set) >= min_support:
        return returned_set
    
        



    
###TODO: print all combinations of index's and build set combos from there... should be much more space effecient


all_intersections = starmap(intersect_minsupp, combinations(tid_list, 2))
all_food_intersections = combinations(food_item_list, 2)

food_intersection_list = list(all_food_intersections)



for index, elem in enumerate(all_intersections): 
    if elem:
        print(pairs_list[index], elem)


#list(intersect_minsupp({2,4,8}, {2,4,8}, {2,4,8,9}))
    
#filtered = filterfalse(lambda x: len(x) < min_support, all_intersections)

#list(filtered)




NameError: name 'pairs_list' is not defined

In [10]:
%load_ext line_profiler
##for some reason, this block isn't printing as expected, but it works within my own code. 

for index, intersection in enumerate(all_intersections):
    print("hello")
    print(index, sorted(intersection))
    print(food_intersection_list[index])
    frequent_item_dict['food_item'] = food_intersection_list[index]
    frequent_item_dict['TID'] = intersection


#print(frequent_item_list)
        
#for index, food_intersection in enumerate(all_food_intersections):
#    print(index, food_intersection)





The line_profiler extension is already loaded. To reload it, use:
  %reload_ext line_profiler
hello
0 [5, 7, 8, 9]
({'bread'}, {'butter'})


NameError: name 'frequent_item_dict' is not defined

In [11]:
### THE ECLAT ALGORITHIM - IN PYTHON  
### BY Allen Roush 
### 6/12/18 

from itertools import combinations, starmap

def eclat(data_dictionary, min_support, num_iterations):
    tid_list = []
    food_item_list = []
    frequent_item_list = []
    
    
    for elem in data_dictionary:
        tid_list.append(data_dictionary[elem]['TID'])
        food_item_list.append(data_dictionary[elem]['food_item'])
        
    for i in range(1, num_iterations):   
        all_intersections = starmap(set.intersection, combinations(tid_list, i))
        all_food_intersections = combinations(food_item_list, i)

        food_intersection_list = list(all_food_intersections)


        for index, intersection in enumerate(all_intersections):
            if len(intersection) >= min_support:
                #print(index, sorted(intersection))
                #print(food_intersection_list[index])
                info = {"food_item": food_intersection_list[index],
                        "TID": intersection}
                frequent_item_list.append(info)
    #return sorted(frequent_item_list, key=lambda k: len(k['food_item']), reverse=True) #sorting unnecessary, doing it to show me the "largest" rules first 
    return(frequent_item_list)
%lprun -f eclat eclat(data_dict2, 2, 5)

In [12]:
eclat(data_dict2,4, 5) # 2 is minimum support, 5 iterations. Output is as expected 

[{'food_item': ({'bread'},), 'TID': {1, 4, 5, 7, 8, 9}},
 {'food_item': ({'butter'},), 'TID': {1, 2, 3, 4, 6, 8, 9}},
 {'food_item': ({'milk'},), 'TID': {3, 5, 6, 7, 8, 9}},
 {'food_item': ({'bread'}, {'butter'}), 'TID': {1, 4, 8, 9}},
 {'food_item': ({'bread'}, {'milk'}), 'TID': {5, 7, 8, 9}},
 {'food_item': ({'butter'}, {'milk'}), 'TID': {3, 6, 8, 9}}]

In [13]:
#The power of pandas own testing library 
list(pd.util.testing.rands_array(8, 8))

['nZxnx7W2',
 '2e4jDox5',
 'BbGi8ISS',
 'oTqs6lwD',
 'IStqQVBJ',
 'yZWqtrlA',
 'dz5adpR4',
 'TmO5LPjw']

In [15]:
import numpy as np

random_num_set_list = []

for i in range(0, 100): # generate 100 random sets 
    random_array = np.random.randint(0,1000,(1000)) # generate a list of 100 TID's with possible numbers between 0 and 1000 
    random_set = set(random_array) #set repersentation makes things easier for my code AND makes sense since we should never have duplicate TIDs
    #sets ALSO are neat because now they're random length which is desierable in a testing function 
    random_num_set_list.append(random_set)

random_num_set_list[0:1]

[{1,
  2,
  3,
  4,
  5,
  6,
  7,
  9,
  10,
  11,
  12,
  14,
  16,
  18,
  19,
  20,
  21,
  22,
  23,
  27,
  28,
  30,
  31,
  32,
  35,
  36,
  39,
  40,
  41,
  43,
  44,
  48,
  50,
  55,
  56,
  59,
  61,
  65,
  66,
  67,
  68,
  69,
  70,
  71,
  72,
  73,
  76,
  77,
  78,
  79,
  80,
  82,
  84,
  85,
  86,
  88,
  89,
  91,
  92,
  93,
  95,
  96,
  97,
  98,
  99,
  101,
  102,
  103,
  104,
  105,
  108,
  110,
  111,
  116,
  118,
  119,
  120,
  121,
  122,
  124,
  125,
  126,
  128,
  129,
  132,
  133,
  134,
  135,
  136,
  137,
  139,
  140,
  141,
  143,
  144,
  146,
  147,
  151,
  152,
  154,
  155,
  157,
  158,
  159,
  160,
  162,
  163,
  164,
  165,
  166,
  168,
  169,
  170,
  171,
  173,
  174,
  175,
  177,
  178,
  179,
  181,
  182,
  184,
  185,
  187,
  188,
  189,
  190,
  191,
  194,
  195,
  196,
  200,
  201,
  202,
  203,
  204,
  205,
  206,
  207,
  208,
  209,
  210,
  211,
  212,
  213,
  215,
  217,
  218,
  223,
  224,
  225,
  226,
  

In [16]:

#100 transactions, with randomized "food items" and random sets of numbers 

rand_item_list = list(pd.util.testing.rands_array(8, 100))

set_list = list(map(lambda x: {x}, rand_item_list))
                      
df1 = pd.DataFrame({'food_item': set_list, 'TID': random_num_set_list})

df1[0:5]

food_item                                                TID
0  {ymre9DVr}  {1, 2, 3, 4, 5, 6, 7, 9, 10, 11, 12, 14, 16, 1...
1  {8adMJzll}  {0, 1, 2, 4, 6, 8, 9, 10, 12, 15, 16, 19, 23, ...
2  {Dy5Ty448}  {1, 2, 4, 5, 7, 8, 9, 11, 14, 16, 17, 18, 19, ...
3  {dYgYPAy8}  {1, 2, 3, 6, 7, 8, 9, 10, 14, 16, 18, 19, 21, ...
4  {9pbQDclj}  {0, 1, 2, 3, 4, 9, 10, 11, 12, 15, 16, 17, 18,...

In [17]:
data_dict3 = df1.to_dict(orient='index') # convert to dictionary format, as this is what my algorithim reads in 

#data_dict3

In [18]:
sorted(eclat(data_dict3, 20, 4), key = lambda k: len(k['food_item']), reverse=True)
# find all freqent patterns with at least 7 transactions in common, ran for 4 iterations. 
#WARNING: as num iterations scales up, performance TANKS and number of operations scales exponentially 

[{'food_item': ({'ymre9DVr'}, {'8adMJzll'}, {'Dy5Ty448'}),
  'TID': {1,
   2,
   4,
   9,
   16,
   19,
   27,
   31,
   32,
   35,
   36,
   41,
   56,
   61,
   66,
   73,
   76,
   77,
   79,
   86,
   88,
   91,
   97,
   108,
   111,
   116,
   119,
   121,
   122,
   124,
   129,
   136,
   141,
   143,
   146,
   155,
   157,
   158,
   159,
   163,
   170,
   177,
   179,
   181,
   187,
   189,
   190,
   194,
   207,
   209,
   211,
   212,
   230,
   233,
   239,
   240,
   242,
   244,
   246,
   252,
   256,
   260,
   262,
   264,
   269,
   270,
   271,
   273,
   281,
   282,
   283,
   285,
   293,
   294,
   296,
   299,
   304,
   305,
   310,
   314,
   316,
   318,
   325,
   326,
   329,
   331,
   340,
   341,
   342,
   347,
   351,
   355,
   356,
   359,
   361,
   362,
   363,
   368,
   370,
   376,
   379,
   380,
   387,
   388,
   389,
   392,
   393,
   394,
   396,
   397,
   400,
   401,
   402,
   404,
   406,
   407,
   409,
   411,
   413,
   419,
 

In [20]:
%%cython --annotate  


from itertools import combinations, starmap


## INCOMPLETE 

cython: boundscheck=False
cython: wraparound=False
cython: profile=True
cython: linetrace=True
cython: infer_types=True
cdef list eclat_cython(dict data_dictionary, unsigned int min_support, unsigned int num_iterations):
    cdef list tid_list = []
    cdef list food_item_list = []
    cdef list frequent_item_list = []
    cdef set tid_set = set()
    cdef set food_set = set()
    cdef int elem
    cdef int index
    cdef int i
    #cdef dict info
    
    
    for elem in data_dictionary:
        tid_set = data_dictionary[elem]['TID']
        food_set = data_dictionary[elem]['food_item']
        tid_list.append(tid_set)
        food_item_list.append(food_set)
        
    for i in range(1, num_iterations):   
        all_intersections = starmap(set.intersection, combinations(tid_list, i))
        all_food_intersections = combinations(food_item_list, i)

        food_intersection_list = list(all_food_intersections)


        for index, intersection in enumerate(all_intersections):
            if len(intersection) >= min_support:
                #print(index, sorted(intersection))
                #print(food_intersection_list[index])
                info = {"food_item": food_intersection_list[index],
                        "TID": intersection}
                frequent_item_list.append(info)
    #return sorted(frequent_item_list, key=lambda k: len(k['food_item']), reverse=True)
    return frequent_item_list

In [17]:
eclat_cython(data_dict2, 2, 5)
#sorted(eclat_cython(data_dict2, 2, 6), key = lambda k: len(k['food_item']), reverse=True)


NameError: name 'eclat_cython' is not defined

In [48]:
%lprun -f eclat_cython eclat_cython(data_dict3, 7, 4)

/home/lain/anaconda3/lib/python3.6/site-packages/line_profiler.py:321: UserWarning: Could not extract a code object for the object <built-in function eclat_cython>
  profile = LineProfiler(*funcs)


In [19]:


%lprun -f eclat eclat(data_dict3, 7, 4)


#eclat_cython(data_dict3, 4, 3)

In [59]:
#%lprun -f eclat eclat(data_dict3, 7, 4) #a "magic" thing in jupyter to make line_profiler work within the notebook. Invaluable for profiling! 
%timeit eclat(data_dict3, 7, 3)

261 ms ± 5.11 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [68]:
%memit eclat_cython(data_dict3, 7, 4)

peak memory: 1455.89 MiB, increment: 0.00 MiB


In [20]:
%memit eclat(data_dict3, 7, 4)

peak memory: 1625.52 MiB, increment: 159.20 MiB
